In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
# !pip install mxnet
# !pip install gluonnlp pandas tqdm
# !pip install sentencepiece
# !pip install transformers==3 # 최신 버전으로 설치하면 "Input: must be Tensor, not str" 라는 에러 발생
# !pip install torch
# !pip install torchmetrics

!pip install git+https://git@github.com/SKTBrain/KoBERT.git@master

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://****@github.com/SKTBrain/KoBERT.git (to revision master) to /tmp/pip-req-build-m3atldel
  Running command git clone -q 'https://****@github.com/SKTBrain/KoBERT.git' /tmp/pip-req-build-m3atldel
     |████████████████████████████████| 129 kB 35.4 MB/s 
     |████████████████████████████████| 344 kB 74.1 MB/s 
     |████████████████████████████████| 54.7 MB 39 kB/s 
     |████████████████████████████████| 4.5 MB 63.7 MB/s 
     |████████████████████████████████| 1.2 MB 63.5 MB/s 
     |██████████████████████████████▎ | 834.1 MB 1.3 MB/s eta 0:00:37tcmalloc: large alloc 1147494400 bytes == 0x3a2bc000 @  0x7f0550d14615 0x5d6f4c 0x51edd1 0x51ef5b 0x4f750a 0x4997a2 0x4fd8b5 0x4997c7 0x4fd8b5 0x49abe4 0x4f5fe9 0x55e146 0x4f5fe9 0x55e146 0x4f5fe9 0x55e146 0x5d8868 0x5da092 0x587116 0x5d8d8c 0x55dc1e 0x55cd91 0x5d8941 0x49abe4 0x55cd91 0x5d8941 0x4990ca 0x5d8868 0x4997a2 0x4fd8b5 

In [ ]:
import torch
from torch import nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
import gluonnlp as nlp
import numpy as np
from tqdm import tqdm, tqdm_notebook

from sklearn.model_selection import train_test_split

from kobert.utils import get_tokenizer
from kobert.pytorch_kobert import get_pytorch_kobert_model

from transformers import AdamW
from transformers.optimization import get_cosine_schedule_with_warmup
import pandas as pd
from tqdm import tqdm_notebook

In [ ]:
##GPU 사용 시
device = torch.device("cuda:0")

bertmodel, vocab = get_pytorch_kobert_model()

from transformers import AutoTokenizer, AutoModelForSequenceClassification

# tokenizer = AutoTokenizer.from_pretrained("snunlp/KR-FinBert-SC")

# model = AutoModelForSequenceClassification.from_pretrained("snunlp/KR-FinBert-SC")

/content/.cache/kobert_v1.zip[██████████████████████████████████████████████████]
/content/.cache/kobert_news_wiki_ko_cased-1087f8699e.spiece[██████████████████████████████████████████████████]


### 데이터 전처리


In [ ]:
import pandas as pd

# 데이터 입력


In [ ]:
df = pd.read_csv('/content/drive/MyDrive/주가원인분석/df_kia_weekday.csv')
df = df[['content', 'target']]
target_dict = {'-2' : '0', '-1' : '1', '0' : '2', '1' : '3', '2' : '4', '3' : '5'}
df['target'] = df['target'].apply(lambda x : target_dict[str(x)])
df['target'] = df['target'].astype('int')
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 11526 entries, 0 to 11525
Data columns (total 2 columns):
 #   Column   Non-Null Count  Dtype 
---  ------   --------------  ----- 
 0   content  11526 non-null  object
 1   target   11526 non-null  int64 
dtypes: int64(1), object(1)
memory usage: 180.2+ KB


In [ ]:
df.head()

content  target
0  국내완성차 11월 판매 76만2천967대전년비 8.4서울연합인포맥스 이민재 기자  ...       1
1  검찰, 에 건넨 특활비 추적해 유의미한 용처 파악서울연합뉴스 방현덕 기자  박근혜 ...       2
2  특징주현대차 3인방 내림세.. 판매부진에 파업 우려이데일리 함정선 기자 현대차그룹 ...       2
3  제네시스 80 디젤 출격임박수입차 수준 연비성능 뽑았다이데일리 노재웅 기자 의 고급...       2
4  이데일리 11월 건설 체감경기 악화정책금리 인상 영향이데일리 1. 최종구 창업중소기...       2

In [ ]:
df['target'].value_counts()

2    4961
1    3313
3    3189
0      32
4      31
Name: target, dtype: int64

In [ ]:
# import re
# for idx in df.index:
#   content = df.loc[idx, 'content']
#   content_pre = re.sub('[^a-zA-Zㄱ-ㅎ가-힣. ]', '', content)
#   df.loc[idx, 'content'] = content_pre
# df.head()

In [ ]:
train_data, test_data = train_test_split(df, test_size=0.2, random_state=2022, stratify=df.target)
train_data.shape, test_data.shape

((9220, 2), (2306, 2))

In [ ]:
train_data_list = []
for i in range(len(train_data)):
  train_data_list.append([train_data.iloc[i,0], train_data.iloc[i,1]])
train_data_list

[['삼성전자기아차전자 등 31개사 동반성장지수 최우수서울연합뉴스 김보경 기자  삼성전자기아자동차전자텔레콤제일제당 등 31개 기업이 중소기업과의 동반성장 노력을 평가한 동반성장지수에서 최우수 등급을 받았다. 반면 타타대우상용차, 한솔섬유 등 7개사는 최하위 등급을 받았다. 동반성장위원회는 27일 서울 서초구 팔래스호텔에서 제55차 동반성장위원회를 개최하고 2018년도 동반성장지수 평가 결과를 확정 공표했다. 공표대상 189개 기업의 동반성장지수를 평가한 결과 최우수 31개사, 우수 64개사, 양호 68개사, 보통 19개사, 미흡 7개사로 집계됐다. 최우수 등급에 포함된 기업은 기아자동차, 네이버, 농심, 대림산업, 대상, 만도, 삼성디스플레이, 삼성전기, 삼성전자, 삼성, 유한킴벌리, 현대건설, 현대모비스, 현대엔지니어링, 현대트랜시스, 호반건설, 제일제당, 건설, , , 디스플레이, 생활건강, 유플러스, 이노텍, 전자, 화학,  , 건설, 종합화학, 주식회사, 텔레콤가나다순이다. 업종별로 보면 정보통신업종의 평가대상 기업 9개사가 모두 우수 이상 등급을 받아 지속해서 강세를 보였다. 건설업종도 6개사가 최우수 등급을 받아 전년 대비 개선된 모습을 보였고, 중견기업은 전년과 동일하게 6개사가 최우수 등급을 땄다. 2017년도와 2018년도 공통으로 평가에 참여한 대기업 171개사 중 등급이 상승한 기업은 33개사19.3로 나타났다. 특히 3년 이상 연속 최우수 등급을 받은 기업은 15개로, 삼성전자8년, 종합화학, 텔레콤이상 7년, 기아자동차6년, 현대트랜시스, , 디스플레이, 생활건강, 주식회사이상 5년, 유한킴벌리, 제일제당, 화학이상 4년, 네이버, 이노텍, 건설이상 3년 등이다. 덕양산업, 서연이화, 서연전자, 에코플라스틱, 이래오토모티브시스템, 타타대우상용차, 한솔섬유 등 7개사는 공정거래협약을 체결하지 않아 미흡 등급을 받았다. 동반성장지수는 대중소기업 간 동반성장 촉진을 목적으로 대기업의 동반성장 수준을 평가하여 계량화한 지표다. 동반위가 2011

In [ ]:
test_data_list = []
for i in range(len(test_data)):
  test_data_list.append([test_data.iloc[i,0], test_data.iloc[i,1]])
test_data_list

[['자동차산업협회 카드수수료 인상, 업계 경영회복 차질서울연합뉴스 김준억 기자  한국자동차산업협회는 5일 자동차업체와 신용카드사 간 수수료율 갈등과 관련해 자동차업계의 경영위기가 악화할 것이란 우려를 담은 의견서를 발표했다. 협회는 카드사들의 수수료 수입은 자동차 구매 때 카드를 사용하는 소비자가 늘어나며 증가하고 있다며 조달금리 하락과 연체비율 감소 등에 따라 수수료율 인상 요인이 없지만, 인상을 강행한 것은 자동차산업에 악재로 작용할 수 있다고 주장했다. 이어 일방적인 수수료율 인상은 자동차업계에 수백억원의 추가 비용을 발생시키고, 이는 고스란히 자동차업계의 수익성 악화로 이어질 것이라며 수수료율 인상이 경영위기 극복에 총력을 기울이는 업계와 정부의 노력에 부정적 영향을 줄 것이라고 지적했다. 협회는 현대차005380의 지난해 자동차 부문 영업이익률이 1.4에 그쳤고 한국은 4년간 3조원의 누적 적자를 기록하는 등 업계의 경영실적이 악화하고 있다고 강조했다. 협회는 자동차업계의 어려운 경영 상황을 고려해 카드사들은 수수료율 인상을 자제할 필요가 있다며 공정하고 합리적인 근거를 바탕으로 수수료율을 책정해야 한다고 밝혔다. 한편, 현대차는 신한삼성국민하나롯데카드 등 5개사에 10일부터, 기아차000270는 11일부터 가맹점 계약을 해지하겠다고 4일 밝혔다. justdustyna.co.kr',
  1],
 ['상승 피로감 코스피 하락 출발3,230선 거래서울연합인포맥스 정지서 기자  코스피가 하락 출발했다. 4일 코스피는 오전 9시 9분 현재 전일보다 14.32포인트0.43 하락한 3,233.11을 기록했다. 간밤 뉴욕증시는 민간 고용 지표 등 긍정적인 경제 지표에도 긴축 우려가 커지며 하락했다. 미국 국채 가격도 5월 비농업 고용보고서 호조 기대, 연방준비제도ed연준의 긴축 경계가 커져 하락세를 보였다. 달러화 가치는 3주 만에 최고치를 기록하며 강세를 보였고, 유가는 휘발유 재고가 예상외로 늘었다는 소식과 차익실현 매물에 보합세로 마쳤다. 장 초반 코스피도

In [ ]:
tokenizer = get_tokenizer()
tok = nlp.data.BERTSPTokenizer(tokenizer, vocab, lower=False)

using cached model. /content/.cache/kobert_news_wiki_ko_cased-1087f8699e.spiece


In [ ]:
class BERTDataset(Dataset):
    def __init__(self, dataset, sent_idx, label_idx, bert_tokenizer, max_len,
                 pad, pair):
        transform = nlp.data.BERTSentenceTransform(
            bert_tokenizer, max_seq_length=max_len, pad=pad, pair=pair) 

        self.sentences = [transform([i[sent_idx]]) for i in dataset]
        self.labels = [np.int32(i[label_idx]) for i in dataset]

    def __getitem__(self, i):
        return (self.sentences[i] + (self.labels[i], ))

    def __len__(self):
        return (len(self.labels))

In [ ]:
max_len = 250 # 해당 길이를 초과하는 단어에 대해선 bert가 학습하지 않음
batch_size = 8
warmup_ratio = 0.1
num_epochs = 50
max_grad_norm = 1
log_interval = 200
learning_rate = 5e-5

In [ ]:
data_train = BERTDataset(train_data_list, 0, 1, tok, max_len, True, False)
data_test = BERTDataset(test_data_list, 0, 1, tok, max_len, True, False)

In [ ]:
# pytorch용 DataLoader 사용
train_dataloader = torch.utils.data.DataLoader(data_train, batch_size=batch_size, num_workers=5)
test_dataloader = torch.utils.data.DataLoader(data_test, batch_size=batch_size, num_workers=5)

/usr/local/lib/python3.8/dist-packages/torch/utils/data/dataloader.py:478: UserWarning: This DataLoader will create 5 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(_create_warning_msg(


In [ ]:
class BERTClassifier(nn.Module):
    def __init__(self,
                 bert,
                 hidden_size = 768,
                 num_classes = 5, # softmax 사용 <- binary일 경우는 2
                 dr_rate=None,
                 params=None):
        super(BERTClassifier, self).__init__()
        self.bert = bert
        self.dr_rate = dr_rate
                 
        self.classifier = nn.Linear(hidden_size , num_classes)
        if dr_rate:
            self.dropout = nn.Dropout(p=dr_rate)
    
    def gen_attention_mask(self, token_ids, valid_length):
        attention_mask = torch.zeros_like(token_ids)
        for i, v in enumerate(valid_length):
            attention_mask[i][:v] = 1
        return attention_mask.float()

    def forward(self, token_ids, valid_length, segment_ids):
        attention_mask = self.gen_attention_mask(token_ids, valid_length)
        
        _, pooler = self.bert(input_ids = token_ids, token_type_ids = segment_ids.long(), attention_mask = attention_mask.float().to(token_ids.device))
        if self.dr_rate:
            out = self.dropout(pooler)
        return self.classifier(out)

In [ ]:
model = BERTClassifier(bertmodel,  dr_rate=0.5).to(device)

In [ ]:
# del model

In [ ]:
# model = BERTClassifier(bertmodel, dr_rate=0.5).to(device)

In [ ]:
# Prepare optimizer and schedule (linear warmup and decay)
no_decay = ['bias', 'LayerNorm.weight']
optimizer_grouped_parameters = [
    {'params': [p for n, p in model.named_parameters() if not any(nd in n for nd in no_decay)], 'weight_decay': 0.01},
    {'params': [p for n, p in model.named_parameters() if any(nd in n for nd in no_decay)], 'weight_decay': 0.0}
]

In [ ]:
# 옵티마이저 선언
optimizer = AdamW(optimizer_grouped_parameters, lr=learning_rate)
loss_fn = nn.CrossEntropyLoss() # softmax용 Loss Function 정하기 <- binary classification도 해당 loss function 사용 가능


In [ ]:
t_total = len(train_dataloader) * num_epochs
warmup_step = int(t_total * warmup_ratio)

In [ ]:
scheduler = get_cosine_schedule_with_warmup(optimizer, num_warmup_steps=warmup_step, num_training_steps=t_total)


In [ ]:
# 학습 평가 지표인 accuracy 계산 -> 얼마나 타겟값을 많이 맞추었는가
def calc_accuracy(X,Y):
    max_vals, max_indices = torch.max(X, 1)
    train_acc = (max_indices == Y).sum().data.cpu().numpy()/max_indices.size()[0]
    return train_acc

In [ ]:
# !pip install torchmetrics==0.6.2

In [ ]:
# from torchmetrics import F1 # import 해줍니다.

# f1 = F1(num_classes=6).to(device) # num_classes의 값으로 6을 주고 인스턴스를 생성합니다

In [ ]:
import os
os.environ['CUDA_LAUNCH_BLOCKING'] = "1"
os.environ["CUDA_VISIBLE_DEVICES"] = "0"

In [ ]:
# checkpoint
from copy import deepcopy
best_acc = 0
best_acc_model = None 

# 모델 학습 시작
for e in range(num_epochs):
    train_acc = 0.0
    test_acc = 0.0
    
    model.train()
    for batch_id, (token_ids, valid_length, segment_ids, label) in enumerate(tqdm_notebook(train_dataloader)):
        optimizer.zero_grad()
        token_ids = token_ids.long().to(device)
        segment_ids = segment_ids.long().to(device)
        valid_length= valid_length
        label = label.long().to(device)
        out = model(token_ids, valid_length, segment_ids)
        loss = loss_fn(out, label)
        loss.backward()
        torch.nn.utils.clip_grad_norm_(model.parameters(), max_grad_norm) # gradient clipping
        optimizer.step()
        scheduler.step()  # Update learning rate schedule
        train_acc += calc_accuracy(out, label)

        if batch_id % log_interval == 0:
            print("epoch {} batch id {} loss {} train acc {} acc {}".format(e+1, batch_id+1, loss.data.cpu().numpy(), train_acc / (batch_id+1), train_acc / (batch_id+1)))
    print("epoch {} train acc {} acc {}".format(e+1, train_acc / (batch_id+1), train_acc / (batch_id+1)))
    
    model.eval() # 평가 모드로 변경
    
    for batch_id, (token_ids, valid_length, segment_ids, label) in enumerate(tqdm_notebook(test_dataloader)):
        token_ids = token_ids.long().to(device)
        segment_ids = segment_ids.long().to(device)
        valid_length= valid_length
        label = label.long().to(device)
        out = model(token_ids, valid_length, segment_ids)
        test_acc += calc_accuracy(out, label)

    if (test_acc / (batch_id+1)) > best_acc:
          best_acc = (test_acc / (batch_id+1))
          best_acc_model = deepcopy(model)  
    
    print("epoch {} test acc {} acc {}".format(e+1, test_acc / (batch_id+1), test_acc / (batch_id+1)))

<ipython-input-32-f7366f6f71d1>:12: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for batch_id, (token_ids, valid_length, segment_ids, label) in enumerate(tqdm_notebook(train_dataloader)):


  0%|          | 0/1153 [00:00<?, ?it/s]

/usr/local/lib/python3.8/dist-packages/torch/utils/data/dataloader.py:478: UserWarning: This DataLoader will create 5 worker processes in total. Our suggested max number of worker in current system is 2, which is smaller than what this DataLoader is going to create. Please be aware that excessive worker creation might get DataLoader running slow or even freeze, lower the worker number to avoid potential slowness/freeze if necessary.
  warnings.warn(_create_warning_msg(


epoch 1 batch id 1 loss 1.2457224130630493 train acc 0.125 acc 0.125
epoch 1 batch id 201 loss 1.0596120357513428 train acc 0.42661691542288555 acc 0.42661691542288555
epoch 1 batch id 401 loss 0.9404078125953674 train acc 0.408354114713217 acc 0.408354114713217
epoch 1 batch id 601 loss 1.0875831842422485 train acc 0.41118968386023297 acc 0.41118968386023297
epoch 1 batch id 801 loss 1.1076371669769287 train acc 0.4052746566791511 acc 0.4052746566791511
epoch 1 batch id 1001 loss 0.9384949803352356 train acc 0.40796703296703296 acc 0.40796703296703296
epoch 1 train acc 0.40698178664353857 acc 0.40698178664353857


<ipython-input-32-f7366f6f71d1>:32: TqdmDeprecationWarning: This function will be removed in tqdm==5.0.0
Please use `tqdm.notebook.tqdm` instead of `tqdm.tqdm_notebook`
  for batch_id, (token_ids, valid_length, segment_ids, label) in enumerate(tqdm_notebook(test_dataloader)):


...

  0%|          | 0/289 [00:00<?, ?it/s]

epoch 5 test acc 0.43079584775086505 acc 0.43079584775086505


  0%|          | 0/1153 [00:00<?, ?it/s]

epoch 6 batch id 1 loss 1.1349949836730957 train acc 0.25 acc 0.25
epoch 6 batch id 201 loss 1.1294106245040894 train acc 0.44527363184079605 acc 0.44527363184079605
epoch 6 batch id 401 loss 1.0584887266159058 train acc 0.41801745635910226 acc 0.41801745635910226


KeyboardInterrupt: ignored

In [ ]:
test_sentence = "저번주는 멘토링이여서 술을 많이 못마셨어. ['SEP'] 이번주는 어떠세요? ['SEP'] 점심에 냉짬뽕에 한잔 하고 저녁에 달리기로 했어 "
test_label = 0 # 실제 질병

In [ ]:
unseen_test = pd.DataFrame([[test_sentence, test_label]], columns = [['질문 내용', '질병명']])
unseen_values = unseen_test.values
test_set = BERTDataset(unseen_values, 0, 1, tok, max_len, True, False)
test_input = torch.utils.data.DataLoader(test_set, batch_size=1, num_workers=5)

for batch_id, (token_ids, valid_length, segment_ids, label) in enumerate(tqdm_notebook(test_input)):
  token_ids = token_ids.long().to(device)
  segment_ids = segment_ids.long().to(device)
  valid_length= valid_length
  out = model(token_ids, valid_length, segment_ids)
  print(out)
  # print(mapping[int(out[0].argmax().cpu().numpy())])
  print('예측감정 :', big_sent_idx_to_dict[int(out[0].argmax().cpu().numpy())] , '\n', '실제감정 :', big_sent_idx_to_dict[test_label])

In [ ]:
# mapping[int(out[0].argmax().cpu().numpy())]

In [ ]:
print(best_f1)

In [ ]:
torch.save(best_f1_model, "/content/drive/MyDrive/Dialog-KoELECTRA/pretrain/setiment_data/model_0714_Bsent_ml250_ep50.pt")

In [ ]:
# bertmodel2, vocab = get_pytorch_kobert_model()

In [ ]:
!pip install numpy --upgrade

In [ ]:
bertmodel2= torch.load('/content/drive/MyDrive/setiment_data/model_0714_SEP_maxlen_250_ep_5.pt')
bertmodel2.eval()

In [ ]:
unseen_test = pd.DataFrame([[test_sentence, test_label]], columns = [['질문 내용', '질병명']])
unseen_values = unseen_test.values
test_set = BERTDataset(unseen_values, 0, 1, tok, max_len, True, False)
test_input = torch.utils.data.DataLoader(test_set, batch_size=1, num_workers=5)

for batch_id, (token_ids, valid_length, segment_ids, label) in enumerate(tqdm_notebook(test_input)):
  token_ids = token_ids.long().to(device)
  segment_ids = segment_ids.long().to(device)
  valid_length= valid_length
  out = bertmodel2(token_ids, valid_length, segment_ids)
  print(out)
  # print(mapping[int(out[0].argmax().cpu().numpy())])
  print('예측감정 :', big_sent_idx_to_dict[int(out[0].argmax().cpu().numpy())] , '\n', '실제감정 :', big_sent_idx_to_dict[test_label])

In [ ]:
'''
총괄모델 1

cl 1     
cl 2
cl 3
cl 4
cl 5
cl 6

평행
softmax와의 개념과는 다르다. 절대값이 크다고 해서 확률이 높다 할 수 있을까?
- 검증이 필요함. 논리적으로 가능/ 불가능의 영역.
'''